U ovoj svesci su isprobani neki od klasičnih modela na podacima koji su očišćeni i pripremljeni za klasifikaciju u prethodnoj svesci.

In [49]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import nltk
from nltk import word_tokenize
from sklearn import model_selection
from sklearn.feature_extraction.text import TfidfVectorizer

from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score, hamming_loss, classification_report, f1_score
from skmultilearn.problem_transform import ClassifierChain
from skmultilearn.adapt import MLkNN

In [50]:
data = pd.read_csv('csv/train_01.csv')

In [51]:
data.head()

id                                       comment_text  toxic  \
0  0000997932d777bf  explan edit made username hardcore metallica f...      0   
1  000103f0d9cfb60f  d'aww! match background colour i'm seemingly s...      0   
2  000113f07ec002fd  hey man, i'm really tri edit war guy constantl...      0   
3  0001b41b1c6bb37e  " can't make real suggest improv wonder sectio...      0   
4  0001d958c54c6e35         you, sir, hero chance rememb page that on?      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0

In [42]:
data[data.isnull().any(axis=1)]
# ovo su komentari koji su bili prazni

id comment_text  toxic  severe_toxic  obscene  threat  \
228     0091798f05a311af          NaN      0             0        0       0   
329     00d300b2a1d61c1c          NaN      0             0        0       0   
3699    09e4ea8663421151          NaN      0             0        0       0   
3990    0aa6f3529219b37e          NaN      0             0        0       0   
4482    0bed2196c873636d          NaN      0             0        0       0   
...                  ...          ...    ...           ...      ...     ...   
153616  9fe2529bbf1aa64a          NaN      0             0        0       0   
154268  ab68b24628bbe30e          NaN      0             0        0       0   
156776  d3741a61f9c91ac0          NaN      0             0        0       0   
158092  e8a55975186094fe          NaN      0             0        0       0   
159315  fbf8672ea3b4ddf7          NaN      1             0        0       0   

        insult  identity_hate  
228          0              0  
329          0              0  
3699         0              0  
3990         0              0  
4482         0              0  
...        ...            ...  
153616       0              0  
154268       0              0  
156776       0              0  
158092       0              0  
159315       0              0  

[118 rows x 8 columns]

In [52]:
data = data.dropna(how='any',axis=0) 

In [53]:
data['comment_text'].isnull().any()

False

In [54]:
data_text = data['comment_text'].values.astype('U')
X = data.drop(labels=['id'], axis=1)
y = data.drop(labels = ['id', 'comment_text'], axis=1)

MemoryError: Unable to allocate 2.97 GiB for an array with shape (159453,) and data type <U5000

Podela na trening i test skupove

In [12]:
X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size = 0.33, random_state=42)

### Feature Engineering

https://www.youtube.com/watch?v=YyOuDi-zSiI

https://medium.com/technovators/machine-learning-based-multi-label-text-classification-9a0e17f88bb4

In [13]:
vectorizer = TfidfVectorizer(strip_accents='unicode', tokenizer=word_tokenize, analyzer='word', ngram_range=(1,3), norm='l2', max_features = 10000)

In [14]:
X_train_vec = vectorizer.fit_transform(X_train['comment_text'])

In [15]:
X_test_vec = vectorizer.transform(X_test['comment_text'])

In [16]:
features = vectorizer.get_feature_names()
features

['!',
 '! !',
 '! ! !',
 "! ! '",
 "! ! ''",
 "! ! 'fuck",
 '! ! )',
 '! ! ``',
 '! ! access',
 '! ! fuck',
 '! ! hi',
 '! ! i',
 '! ! jim',
 '! ! person',
 '! ! please',
 '! ! u',
 "! '",
 "! ' u",
 "! ''",
 "! '' ''",
 "! 'fuck",
 "! 'fuck you",
 '! (',
 '! ( talk',
 '! )',
 '! ) ,',
 '! ) ``',
 '! ,',
 '! ?',
 '! ? !',
 '! ``',
 '! `` ``',
 '! access',
 '! access deneid',
 '! also',
 '! block',
 '! block you',
 '! bunksteve',
 '! bunksteve gay',
 '! eat',
 '! eat cock',
 '! f',
 '! f uu',
 '! fuck',
 '! fuck all',
 '! fuck bitch',
 '! fuck cocksuck',
 '! fuck fired',
 '! fuck you',
 '! get',
 '! go',
 '! go fuck',
 '! good',
 '! haahhahahah',
 '! haahhahahah yaaa',
 '! heil',
 '! heil hitler',
 '! hello',
 '! hello ,',
 '! hi',
 '! hi wikipedia',
 '! hope',
 '! i',
 "! i 'm",
 "! i 've",
 '! in',
 '! in name',
 '! jim',
 '! jim wale',
 '! know',
 '! know you',
 '! lol',
 '! look',
 '! mangina',
 '! mangina !',
 '! mothjer',
 '! mothjer fucker',
 '! oh',
 '! oh bob',
 '! old',
 '! ol

In [17]:
vectorizer.vocabulary_

{'``': 1401,
 'image': 5076,
 'copyright': 3142,
 'problem': 7238,
 'gif': 4559,
 'thank': 8807,
 'upload': 9227,
 'identifi': 5052,
 'specifi': 8327,
 'status': 8413,
 ',': 587,
 'requir': 7664,
 'wikipedia': 9657,
 'policy': 7102,
 'indicate': 5191,
 'imag': 5073,
 'descript': 3504,
 'page': 6694,
 'use': 9249,
 'appropriate': 1945,
 'tag': 8643,
 'may': 5958,
 'delet': 3415,
 'time': 8956,
 'next': 6338,
 'seven': 8042,
 'day': 3342,
 'images': 5102,
 'please': 7007,
 'verify': 9396,
 'provid': 7308,
 'inform': 5205,
 'well': 9580,
 'see': 7947,
 'follow': 4311,
 'autom': 2203,
 'notice': 6452,
 'assistance': 2149,
 'media': 6013,
 'question': 7365,
 'hi': 4853,
 'ad': 1624,
 'fair': 4126,
 'seem': 7981,
 'subject': 8496,
 'howev': 4959,
 'need': 6278,
 'state': 8399,
 'source': 8274,
 'own': 6675,
 'cool': 3132,
 'way': 9523,
 'thanks': 8838,
 '!': 0,
 'sockpuppet': 8215,
 'think': 8889,
 'move': 6178,
 'talk': 8691,
 'one': 6568,
 'longer': 5782,
 '(': 405,
 'the': 8850,
 'main': 

In [18]:
#from yellowbrick.text import FreqDistVisualizer
#visualizer = FreqDistVisualizer(features=features, orient='v')
#visualizer.fit(X_train_vec)
#visualizer.show()

Čuvamo vectorizer i učitavamo za ponovnu upotrebu

In [19]:
import pickle

# pickle.dump(vectorizer, open("vectorizer_01.pickle", "wb"))

In [46]:
loaded_vectorizer = pickle.load(open("vectorizer_01.pickle", "rb"))

OneVsRest classifier

In [20]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.svm import LinearSVC

clf = OneVsRestClassifier(LinearSVC(), n_jobs=1)

In [21]:
clf.fit(X_train_vec, y_train)

OneVsRestClassifier(estimator=LinearSVC(), n_jobs=1)

In [22]:
score = clf.score(X_train_vec, y_train)

In [23]:
pred = clf.predict(X_test_vec)

In [24]:
score

0.9390076100081436

Tacnost je 0.93 na trening skupu i 0.91 na test skupu, ali to nije značajna mera za nabalansirane skupove podataka.

In [26]:
clf.score(X_test_vec,y_test)

0.9172557962751805

F1 mera: 

In [27]:
print(f1_score(y_test, pred, average='weighted'))

0.6957374753457446

In [55]:
#k = 0
#for p in pred:
 #   if p[0] ==1 or p[1] == 1 or p[2]==1 or  p[3]==1:
 #      print(p)
 #       print(X_test.iloc[k])
 #   k= k+1    


In [38]:
# test.csv, spajanje kolona i izbacivanje onih koji se ne koriste za proveru

test_unseen = pd.read_csv('csv/test_01.csv')
test_labels = pd.read_csv('csv/test_labels.csv')

test_text = test_unseen['comment_text'].values.astype('U')

unseen_data = pd.merge(test_unseen,test_labels,on="id")
unseen_data = unseen_data.dropna(how='any',axis=0)
unseen_data = unseen_data[unseen_data["toxic"] != -1]
unseen_data

id                                       comment_text  \
5       0001ea8717f6de06  thank understand think highly would revert wit...   
7       000247e83dcc1211                             dear god site horrible   
11      0002f87b16116a7f  " somebody invariably try add religion? really...   
13      0003e1cccfd5a40a  " say right type ""type"" institut need case t...   
14      00059ace3e3e9a53  " ad new product list, make sure relev ad new ...   
...                  ...                                                ...   
153150  fff8f64043129fa2  jerome, see never got around ! surpris look ex...   
153151  fff9d70fe0722906         lucky bastard heh famous kida envy congrat   
153154  fffa8a11c4378854               shame all!!! want speak gay romanian   
153155  fffac2a094c8e0e2  mel gibson nazi bitch make shitty movie much b...   
153156  fffb5451268fb5ba  " unicorn lair discovery supposedly, unicorn l...   

        toxic  severe_toxic  obscene  threat  insult  identity_hate  
5           0             0        0       0       0              0  
7           0             0        0       0       0              0  
11          0             0        0       0       0              0  
13          0             0        0       0       0              0  
14          0             0        0       0       0              0  
...       ...           ...      ...     ...     ...            ...  
153150      0             0        0       0       0              0  
153151      0             0        0       0       0              0  
153154      0             0        0       0       0              0  
153155      1             0        1       0       1              0  
153156      0             0        0       0       0              0  

[63711 rows x 8 columns]

In [31]:
y_unseen = unseen_data.drop(labels = ['id', 'comment_text'], axis=1)
X_test_unseen = vectorizer.transform(unseen_data['comment_text'])

In [32]:
pred_unseen =  clf.predict(X_test_unseen)

In [33]:
clf.score(X_test_unseen,y_unseen)

0.8813548680761564

Tačnost na test skupu koji se koristi za proveru je niža, 88%

In [34]:
k = 0
for p in pred_unseen:
    if p[0] ==1 or p[1] == 1 or p[2]==1 or  p[3]==1:
        print(p)
        print(unseen_data.iloc[k])
    k= k+1    

[1 0 0 0 0 0]
id                     000247e83dcc1211
comment_text     dear god site horrible
toxic                                 0
severe_toxic                          0
obscene                               0
threat                                0
insult                                0
identity_hate                         0
Name: 7, dtype: object
[1 0 1 0 1 0]
id                                                001068b809feee6b
comment_text     " balance page one sentence basic definit word...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 38, dtype: object
[1 0 1 0 1 0]
id                                        0013fed3aeae7

Name: 2176, dtype: object
[1 0 1 0 0 0]
id                                                03c45b72d38c1f75
comment_text     fuck fuck fuck fuck fuck fuck fuck fuck fuck f...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 2179, dtype: object
[1 1 1 0 1 1]
id                                                03c6344729c4e665
comment_text     azerbaijani proud ramil safarov opportunity ci...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                           

id                                              064fc439dcb1100e
comment_text     dude article suck please list part motherboard?
toxic                                                          0
severe_toxic                                                   0
obscene                                                        0
threat                                                         0
insult                                                         0
identity_hate                                                  0
Name: 3677, dtype: object
[1 0 1 0 0 0]
id                                                065f2cbeb6b49d25
comment_text     " ""bull"" ""bullshit"" unrel ""bull"" mean ""...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                

Name: 5409, dtype: object
[1 0 0 0 1 0]
id                    091f166fbaefa8bb
comment_text     top ten reason retard
toxic                                0
severe_toxic                         0
obscene                              0
threat                               0
insult                               0
identity_hate                        0
Name: 5411, dtype: object
[1 0 0 0 1 0]
id                093ea9c88a986054
comment_text     stupid me, source
toxic                            1
severe_toxic                     0
obscene                          0
threat                           0
insult                           1
identity_hate                    0
Name: 5484, dtype: object
[1 0 0 0 1 0]
id                       095987c5bcd89086
comment_text     people incredibly stupid
toxic                                   1
severe_toxic                            0
obscene                                 1
threat                                  0
insult                              

Name: 7232, dtype: object
[1 0 1 0 0 0]
id                                                0c2f6b30ae8bd242
comment_text     " no, know that, i'll get around watch soon ) ...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 7238, dtype: object
[1 0 0 0 0 0]
id                                                0c30712744c4f10d
comment_text     hey kersey! wut r u ??? whatev gosh black girl...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                           

...

id                      f442fd628e7c89ca
comment_text     get life, fuck cocksuck
toxic                                  1
severe_toxic                           0
obscene                                1
threat                                 0
insult                                 1
identity_hate                          0
Name: 146111, dtype: object
[1 0 1 0 1 0]
id                                             f44bd2735bb45843
comment_text     he fuck crybaby! that nickname crybaby crosby!
toxic                                                         1
severe_toxic                                                  0
obscene                                                       1
threat                                                        0
insult                                                        1
identity_hate                                                 0
Name: 146135, dtype: object
[1 0 0 0 0 0]
id               f4545595a782c7f8
comment_text                hell?
toxic   

id                                                f6cf005acedc8bd8
comment_text     " risneg (""rice nigger"") swedish, highly off...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           1
identity_hate                                                    1
Name: 147647, dtype: object
[1 0 1 0 1 0]
id                                                f6e8bba749609a7c
comment_text     fuck like us neo nazi chance change history, t...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult              

Name: 149138, dtype: object
[1 0 0 0 0 0]
id                                                f956590b0a8e856d
comment_text     let call think fair call thing fact bunch whin...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 149164, dtype: object
[1 0 0 0 0 0]
id                                                f9682073f50ed839
comment_text     sound inappropriate dude, hell talk seen pictu...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                       

Name: 150905, dtype: object
[1 0 0 0 0 0]
id                                                fc4667a971259486
comment_text     that enough bulli last time seek help way bull...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 150907, dtype: object
[1 0 0 0 0 0]
id               fc493d42f9b3cc3f
comment_text      hate country!!!
toxic                           1
severe_toxic                    0
obscene                         0
threat                          0
insult                          0
identity_hate                   0
Name: 150915, dtype: object
[1 0 1 0 1 0]
id               fc4abc835992a728
comment_text                 suc

Name: 152147, dtype: object
[1 0 0 0 0 0]
id                                                fe4cc0283a0b7e5d
comment_text     torment got inform wrong doen't die fifth book...
toxic                                                            0
severe_toxic                                                     0
obscene                                                          0
threat                                                           0
insult                                                           0
identity_hate                                                    0
Name: 152171, dtype: object
[1 0 1 0 1 0]
id                                                fe521f3488ad770a
comment_text     shit bad word shit swearword example shit use ...
toxic                                                            1
severe_toxic                                                     0
obscene                                                          1
threat                                       

### ClassifierChain
 Pristup za multi-label klasifikaciju koristeci ClassifierChain metodu.

In [47]:
classifier = ClassifierChain(LinearSVC())
classifier.fit(X_train_vec, y_train)
#pickle.dump(classifier, open("ClassifierChain_LinearSVC.pickle", "wb"))

MemoryError: Unable to allocate 7.96 GiB for an array with shape (106833, 10000) and data type float64

In [ ]:
score = clf.score(X_test_vec,y_test)
score

In [ ]:
pred = classifier.predict(X_test_vec)

In [ ]:
pred_array = pred.toarray()

In [ ]:
f1_score(y_test, pred_array, average='weighted')

 Iako je score dobijen za dati klasifikator poprilicno velik, 
f1 mera i matrica konfuzije pokazuju da klasifikator ne radi toliko dobro, 
 vec da je doslo do preprilagodjavanja neklasifikovanim podacima.

In [ ]:
from sklearn.metrics import multilabel_confusion_matrix

In [ ]:
confusion = multilabel_confusion_matrix(y_test, pred_array)
confusion

### Balansiranje podataka

Pošto imamo previše podataka koji ne pripadaju nijednoj klasi (komentari koji nisu uvredljivi), uradićemo undersampling tih podataka i izjednačiti sa brojem elemenata u najbrojnijoj klasi

In [ ]:
largest_class_size = (data[classes].sum()).max()
data_balanced = data[~data['id'].isin(dropped_rows['id'])]

In [ ]:
def balance_data(data):
    classes = ['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']
    largest_class_size = (data[classes].sum()).max()
    unclassified_data = data[(data['toxic'] == 0) & (data['severe_toxic'] == 0) & (data['obscene'] == 0) & (data['threat'] == 0) & (data['insult'] == 0) & (data['identity_hate'] == 0)] 
    dropped_rows = unclassified_data.sample(unclassified_data.shape[0] - largest_class_size)
    data_balanced = data[~data['id'].isin(dropped_rows['id'])]
    return data_balanced
    
    

In [ ]:
data_balanced = balance_data(data)

In [ ]:
data_balanced.to_csv('csv/train_02.csv', index = False)

In [ ]:
def feature_selection_and_vectorization(data):
    data_text = data['comment_text'].values.astype('U')
    X = data.drop(labels=['id'], axis=1)
    y = data.drop(labels = ['id', 'comment_text'], axis=1)
    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size = 0.33, random_state=42)
    vectorizer = TfidfVectorizer(strip_accents='unicode', tokenizer=word_tokenize, analyzer='word', ngram_range=(1,3), norm='l2', max_features = 10000)
    X_train_vec = vectorizer.fit_transform(X_train['comment_text'])
    X_test_vec = vectorizer.transform(X_test['comment_text'])
    #pickle.dump(vectorizer, open("vectorizer_balanced.pickle", "wb"))
    return X_train_vec, X_test_vec, y_train, y_test

In [ ]:
X_train_balanced, X_test_balanced, y_train_balanced, y_test_balanced = feature_selection_and_vectorization(data_balanced)

In [ ]:
X_train_balanced

### OneVsRestClassifier

In [48]:
clf = OneVsRestClassifier(LinearSVC(), n_jobs=1)
clf.fit(X_train_balanced, y_train_balanced)
#pickle.dump(clf, open("OneVsRestClassifier_LinearSVC_balanced.pickle", "wb"))
clf = pickle.load(open("OneVsRestClassifier_LinearSVC_balanced.pickle", "rb"))
pred = clf.predict(X_test_balanced)
print(clf.score(X_test_balanced,y_test_balanced))
print(f1_score(y_test_balanced, pred, average='weighted'))

NameError: name 'X_train_balanced' is not defined

### ClassifierChain

In [ ]:
classifier = ClassifierChain(LinearSVC())
classifier.fit(X_train_balanced, y_train_balanced)
#pickle.dump(classifier, open("ClassifierChain_LinearSVC_balanced.pickle", "wb"))
print(clf.score(X_test_balanced,y_test_balanced))
pred = classifier.predict(X_test_balanced)
pred_array = pred.toarray()
print(f1_score(y_test_balanced, pred_array, average='weighted'))

In [ ]:
# Sada je accuracy 0.63 

In [ ]:
confusion = multilabel_confusion_matrix(y_test_balanced, pred_array)
confusion